# Capstone Project - Barcelona's Battle of the Neighborhoods
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction1)
* [Data](#data1)
* [Methodology](#methodology1)
* [Analysis](#analysis1)
* [Results and Discussion](#results1)
* [Conclusion](#conclusion1)


## Introduction: Business Problem <a name="introduction1"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Italian restaurant** in **Barcelona**, Spain.

Since there are lots of restaurants in Barcelona we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Polish restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data1"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to other popular placer in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* District centres of candidate areas will be obtained using **Barcelona Open Data source** from Local authorities.
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Barcelona center will be obtained using **Barcelona Open Data source** of city centre location (Plaza Catalunya) and the main Districts.

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods using the District coordinates provided by the Barcelona Open Data source.

Let's first find the latitude & longitude of Barcelona city center, using specific, well known address and Foursquare API.

### Import necessary Libraries

In [85]:
conda install -c anaconda wget


Solving environment: done

## Package Plan ##

  environment location: /Users/rafadiazrios/opt/anaconda3

  added / updated specs:
    - wget


The following packages will be SUPERSEDED by a higher-priority channel:

  ca-certificates    conda-forge::ca-certificates-2020.6.2~ --> anaconda::ca-certificates-2020.1.1-0
  certifi            conda-forge::certifi-2020.6.20-py37hc~ --> anaconda::certifi-2020.6.20-py37_0
  conda              conda-forge::conda-4.8.3-py37hc8dfbb8~ --> anaconda::conda-4.8.3-py37_0
  openssl            conda-forge::openssl-1.1.1g-h0b31af3_0 --> anaconda::openssl-1.1.1g-h1de35cc_0


Preparing transaction: done
Verifying transaction: done
Executing transaction: done

Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /Users/rafadiazrios/opt/anaconda3

  added / updated specs:
    - geopy


The following packages will be UPDATED:

  ca-certificates      anaconda::ca-certificates-2020.1.1-0 --> conda-forge::ca-certificates-2020.6.20-hecda079_0
  conda                        anaconda::conda-4.8.3-py37_0 --> conda-forge::conda-4.8.3-py37hc8dfbb8_1

The following packages will be SUPERSEDED by a higher-priority channel:

  certifi                anaconda::certifi-2020.6.20-py37_0 --> conda-forge::certifi-2020.6.20-py37hc8dfbb8_0
  openssl               anaconda::openssl-1.1.1g-h1de35cc_0 --> conda-forge::openssl-1.1.1g-h0b31af3_0


Preparing transaction: done
Verifying transaction: done
Executing transaction: done
Solving environment: done

# All requested packages already installed.

Libraries imported.


In [3]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Folium installed
Libraries imported.


In [4]:
import matplotlib.pyplot as plt # plotting library
# backend for rendering plots within the browser
%matplotlib inline 

from sklearn.cluster import KMeans 
from sklearn.datasets.samples_generator import make_blobs

print('Libraries imported.')

Libraries imported.


/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.datasets.samples_generator module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.datasets. Anything that cannot be imported from sklearn.datasets is now part of the private API.
  warnings.warn(message, FutureWarning)


### Import JSON file for Barcelona

#### Import from Area Metropolitana de Barcelona website:
https://geoportalcartografia.amb.cat/AppGeoportalCartografia2/DadesAplicacio/Geoserveis/ca/default.html


In [5]:
#bcn_data = "/Users/rafadiazrios/Coursera Jupyter DS & PY learning/Course 9 - Capstone project/districtes_i_barris_170705.json"
#print('Data downloaded!')

bcn_geodata = "/Users/rafadiazrios/Coursera Jupyter DS & PY learning/Course 9 - Capstone project/bcn_UNITATS_ADM_PUNTS.json"
print('Data2 downloaded!')

Data2 downloaded!


In [6]:
with open('bcn_UNITATS_ADM_PUNTS.json') as json_data:
    barna_data = json.load(json_data)

In [ ]:
# The code was removed by Watson Studio for sharing.

In [15]:
neighborhoods_data = barna_data['features']

Let's take a look at the first item in this list.

In [87]:
neighborhoods_data[0]


{'type': 'Feature',
 'id': 0,
 'geometry': {'type': 'Point',
  'coordinates': [424861.74899999984, 4581559.359999999]},
 'properties': {'FID': 0,
  'ID_ANNEX': '01',
  'ANNEXDESCR': 'Grup - I',
  'ID_TEMA': '0104',
  'TEMA_DESCR': 'Unitats Administratives',
  'ID_CONJ': '010411',
  'CONJ_DESCR': 'Terme Municipal',
  'ID_SUBCONJ': '01041101',
  'SCONJDESCR': 'Terme Municipal',
  'ID_ELEMENT': '0104110104',
  'ELEM_DESCR': 'Noms municipis veïns',
  'NIVELL': 'ADM_01_aux_RT',
  'NDESCR_CA': 'Noms municipis veïns',
  'NDESCR_ES': 'Nombres municipios vecinos',
  'NDESCR_EN': 'Names neighboring municipalities',
  'DISTRICTE': '-',
  'BARRI': '-',
  'TERME': '080771',
  'AEB': '-',
  'SEC_CENS': '-',
  'GRANBARRI': '-',
  'ZUA': '-',
  'CODI_UA': '080771',
  'TIPUS_UA': 'TERME',
  'NOM': 'Esplugues de Llobregat',
  'WEB1': ' ',
  'WEB2': ' ',
  'WEB3': ' ',
  'LITERAL': '080771',
  'ANGLE_TXT': 285}}

In [17]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [18]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [19]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['TIPUS_UA'] 
    neighborhood_name = data['properties']['NOM']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [ ]:
# The code was removed by Watson Studio for sharing.

### Let's slice the dataframe to select only the districts of Barcelona city

In [20]:
bcncity_data = neighborhoods[neighborhoods['Borough'] == 'BARRI'].reset_index(drop=True)
bcncity_data.head(10)

Borough                           Neighborhood      Latitude    Longitude
0   BARRI                               el Raval  4.581121e+06  430624.9313
1   BARRI                         el Barri Gòtic  4.581289e+06  431291.4440
2   BARRI                         la Barceloneta  4.581448e+06  432355.6530
3   BARRI  Sant Pere, Santa Caterina i la Ribera  4.581984e+06  431707.9381
4   BARRI                          el Fort Pienc  4.583261e+06  431580.2748
5   BARRI                     la Sagrada Família  4.584175e+06  431275.9502
6   BARRI                 la Dreta de l'Eixample  4.582931e+06  430582.0822
7   BARRI        l'Antiga Esquerra de l'Eixample  4.582208e+06  429278.2125
8   BARRI         la Nova Esquerra de l'Eixample  4.581700e+06  428919.9315
9   BARRI                            Sant Antoni  4.581114e+06  429725.6300

In [21]:
bcncity_data.shape

(75, 4)

## Define Foursquare Credentials and Version

#### Make sure that you have created a Foursquare developer account and have your credentials handy


In [22]:
# The code was removed by Watson Studio for sharing.

Your credentials:
CLIENT_ID: 0SNKFIVOMYF1JOTTLWIRLO55QF11PAMDVGXXQ3OGZFMBYE53
CLIENT_SECRET:3TJE0KSUGPF0ZXYZQUS4HRRLMFSUQ403Q4WMSPZD2SDEOG4F


In [127]:
# The code was removed by Watson Studio for sharing.

## Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. 

Let's first find the latitude & longitude of Berlin city center, using specific, well known address and Foursquare API

### Let's get the coordinates of the place we would like to explore



In [24]:
#address = 'Plaza Catalunya, Barcelona, Spain'
address = 'Plaza de Catalunya, Barcelona, Spain'
geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print(location)
print(latitude, longitude)

Plaça de Catalunya, la Dreta de l'Eixample, Eixample, Ciutat Vella, Barcelona, Barcelonès, Barcelona, Catalunya, 08001, España
41.3861586 2.169774


In [25]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
barcelona_center = get_coordinates(api_key, address)
print('Coordinate of {}: {}'.format(address, barcelona_center))

Coordinate of Plaza de Catalunya, Barcelona, Spain: [41.3870154, 2.1700471]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Plaza de Catalunya. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [26]:
!pip install shapely

In [27]:
!pip install pyproj

In [28]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Barcelona center longitude={}, latitude={}'.format(longitude, latitude))
x, y = lonlat_to_xy(longitude, latitude)
print('Barcelona center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Barcelona center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Barcelona center longitude=2.169774, latitude=41.3861586
Barcelona center UTM X=430585.515902288, Y=4581958.275650984
Barcelona center longitude=2.1697740000000003, latitude=41.3861586


/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


In [29]:
#address = 'Plaza Catalunya, Barcelona, Spain'
barcelona_center = (latitude,longitude)
print('Coordinate of {}: {}'.format(address, barcelona_center))

Coordinate of Plaza de Catalunya, Barcelona, Spain: (41.3861586, 2.169774)


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [30]:
barcelona_center_x, barcelona_center_y = lonlat_to_xy(barcelona_center[1], barcelona_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = barcelona_center_x - 6000
x_step = 600
y_min = barcelona_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(barcelona_center_x, barcelona_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site

364 candidate neighborhood centers generated.


/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_laun

In [30]:
print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [33]:
map_barcelona = folium.Map(location=barcelona_center, zoom_start=13)
folium.Marker(barcelona_center, popup='Plaza Catalunya').add_to(map_barcelona)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_barcelona)
    #folium.Marker([lat, lon]).add_to(map_berlin)
map_barcelona

## Let's install folium

#### Let's visualize our well known address on the map

In [31]:
print(latitude, longitude)
venues_map = folium.Map(location=[latitude, longitude], zoom_start=16) # generate map centred Bcn Center


# add Center as a red circle mark
folium.features.CircleMarker(
    [latitude, longitude],
    radius=6,
    popup='Center',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
    ).add_to(venues_map)

venues_map

41.3861586 2.169774


OK, we now have the coordinates of centers of districts/areas to be evaluated from Plaza Catalunya as per our locations dataframe.


In [33]:
bcncity_data.head()
#bcncity_data.shape


Borough                           Neighborhood      Latitude    Longitude
0   BARRI                               el Raval  4.581121e+06  430624.9313
1   BARRI                         el Barri Gòtic  4.581289e+06  431291.4440
2   BARRI                         la Barceloneta  4.581448e+06  432355.6530
3   BARRI  Sant Pere, Santa Caterina i la Ribera  4.581984e+06  431707.9381
4   BARRI                          el Fort Pienc  4.583261e+06  431580.2748

In [34]:

def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(api_key, barcelona_center[0], barcelona_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(barcelona_center[0], barcelona_center[1], addr))

Reverse geocoding check
-----------------------
Address of [41.3861586, 2.169774] is: Pl. de Catalunya - Bergara, 08002 Barcelona, Spain


In [35]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Spain', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [36]:
addresses[150:170]

['Spain',
 'Spain',
 'Spain',
 'Avinguda Diagonal, 695, 08028 Barcelona',
 'Av. Dr. Marañón, 19, 08028 Barcelona',
 'Av. de Joan XXIII, 1, 08028 Barcelona',
 'Travessera de les Corts, 142, 08028 Barcelona',
 'Av. de Madrid, 208, 08014 Barcelona',
 'Carrer de Numància, 7, 08029 Barcelona',
 'Carrer de València, 62, 08015 Barcelona',
 'Carrer de la Diputació, 108, 08015 Barcelona',
 'Carrer de Floridablanca, 144, 08011 Barcelona',
 'Carrer Doctor Fleming, 9999, 08001 Barcelona',
 'Baixada de Sant Miquel, 8, 08002 Barcelona',
 'Carrer Pas Sota Murllas, 2, 08003 Barcelona',
 'Passeig de Salvat Papasseit, 18, 08003 Barcelona',
 'Escullera de Poblenou, 1, 08005 Barcelona',
 'Escullera de Poblenou, 167, 08005 Barcelona',
 'Escullera de Poblenou, 6, 08005 Barcelona',
 'Escullera de Poblenou, 2, 08005 Barcelona']

In [50]:
# @hidden cell
#addresses

Looking good. Let's now place all this into a Pandas dataframe.

In [37]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0                 Dàrsena Sud, 08040 Barcelona  41.334521   2.148919   
1           Ml Inflamables, 4, 08040 Barcelona  41.334574   2.156088   
2         Carrer del Port de Ningbó, Barcelona  41.334626   2.163258   
3                                        Spain  41.334678   2.170428   
4                                        Spain  41.334730   2.177598   
5                                        Spain  41.334781   2.184768   
6                                        Spain  41.334831   2.191938   
7                Unnamed Road, 08040 Barcelona  41.339121   2.138102   
8  Via Circulació del Nord, 8, 08040 Barcelona  41.339175   2.145272   
9           Ml Inflamables, 1, 08040 Barcelona  41.339228   2.152443   

               X             Y  Distance from center  
0  428785.515902  4.576243e+06           5992.495307  
1  429385.515902  4.576243e+06           5840.376700  
2  429985.515902  4.576243e+06           5747.173218  
3  430585.515902  4.576243e+06           5715.767665  
4  431185.515902  4.576243e+06           5747.173218  
5  431785.515902  4.576243e+06           5840.376700  
6  432385.515902  4.576243e+06           5992.495307  
7  427885.515902  4.576762e+06           5855.766389  
8  428485.515902  4.576762e+06           5604.462508  
9  429085.515902  4.576762e+06           5408.326913

In [39]:
#...and let's now save/persist this data into local file.
df_locations.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

In [40]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues
# food_category = '52e81612bcbc57f1066b7a04' # Root category for Polish restaurant

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'bar', 'pub']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Barcelona', '')
    address = address.replace(', Germany', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [41]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('italian_restaurants_350.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Restaurant data loaded.


In [42]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 2573
Total number of Italian restaurants: 163
Percentage of Italian restaurants: 6.34%
Average number of restaurants in neighborhood: 13.847222222222221


In [43]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('5a4e98dcd03360688d95dd73', 'Kobuta Ramen', 41.36986017860928, 2.1331966064726955, 'Súria, 8, 08014 Barcelona Cataluña, España', 330, False, 427509.1859078528, 4580178.795731767)
('4c0b8cd5009a0f47273cebbf', 'La Bodegueta de Cal Pep', 41.37377596464733, 2.1323718328933725, 'Canalejas, 12, Barcelona Cataluña, España', 198, False, 427444.56070112495, 4580614.209745048)
('4d02751568e38eec7167dfc4', 'Mson', 41.37280423695585, 2.128722454223953, 'C. Bacardí, 31 (C. Sugranyes), 08028 Barcelona Cataluña, España', 251, False, 427138.2938704959, 4580509.391376183)
('59419af506fb6007376c90ec', 'Amassame', 41.375023, 2.1327457, 'Carrer de Santa Medir 8, 08028 Barcelona Cataluña, España', 254, True, 427477.2108730002, 4580752.340675035)
('4e75111dae60c32850f7bfc0', 'El Candil', 41.37168651011002, 2.129189266294637, 'Pavia, 76 (Carreras Candi), Barcelona Cataluña, España', 315, False, 427176.08540046006, 4580384.9109116)
('4dbd59f443a1d8504ba2ddbe', 

In [44]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('59419af506fb6007376c90ec', 'Amassame', 41.375023, 2.1327457, 'Carrer de Santa Medir 8, 08028 Barcelona Cataluña, España', 254, True, 427477.2108730002, 4580752.340675035)
('4b689a67f964a52058822be3', 'La Briciola', 41.373719, 2.136506, 'Olzinelles, 19, 08014 Barcelona Cataluña, España', 202, True, 427790.22095180367, 4580604.43325217)
('4ba37733f964a5206c3f38e3', 'Teta de Monja', 41.37609405654974, 2.1388755859792195, 'Pl. Osca, 2, 08014 Barcelona Cataluña, España', 261, True, 427990.9993548109, 4580866.136735985)
('4b6363cdf964a52063762ae3', 'Il Golfo di Napoli', 41.372321, 2.155362, 'Carrer Lleida 38, 08004 Barcelona Cataluña, España', 299, True, 429365.5584492378, 4580433.692575301)
('5a359979535d6f0cd0798a9f', 'Macchina', 41.375325418929144, 2.161080653801404, 'Parlament 1, 08015 Barcelona Cataluña, España', 320, True, 429847.02426497947, 4580762.593603634)
('4b58677df964a5203f5628e3', 'La Bella Napoli', 41.37434432358266, 2

In [45]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: bcnKITCHEN, La Paradeta, Llamber, La Ciudadela, Murivecchi, Taquería Canta Y No Llores, Bar Celta Pulpería, Buon Appetito
Restaurants around location 102: Rincón de Galicia
Restaurants around location 103: Ninoska Restaurante, TaTeTí, Els Pollos de Llull, Pizzeria Roma, Rincón de Galicia, Bar de Baix, Restaurant Terrari, Sushi 10
Restaurants around location 104: Restaurant Ají, Ninoska Restaurante, TaTeTí, Ugarit, Curry Barcelona, Enoteca, Barnabier, Jerusalem Restaurante - Shisha Bar
Restaurants around location 105: La Barca del Salamanca, La Fonda del Port Olímpic, El Tinglado, La Taberna Gallega, El Cangrejo Loco, El Rey  de La Gamba II, Ugarit, مطعم خليجيه - Khalijia (Khalijia)
Restaurants around location 106: La Grangeta, Can Fusté, Aire, Restaurante La Traviata, Bar Bayo, Glub, La Granja de Santander, Cafeteteria Tanatori Les Corts
Restaurants around location 107: Punta Anguila, Leku, Setze, 

In [87]:
# @hidden cell
restaurants


{'5a4e98dcd03360688d95dd73': ('5a4e98dcd03360688d95dd73',
  'Kobuta Ramen',
  41.36986017860928,
  2.1331966064726955,
  'Súria, 8, 08014 Barcelona Cataluña, España',
  330,
  False,
  427509.1859078528,
  4580178.795731767),
 '4c0b8cd5009a0f47273cebbf': ('4c0b8cd5009a0f47273cebbf',
  'La Bodegueta de Cal Pep',
  41.37377596464733,
  2.1323718328933725,
  'Canalejas, 12, Barcelona Cataluña, España',
  198,
  False,
  427444.56070112495,
  4580614.209745048),
 '4d02751568e38eec7167dfc4': ('4d02751568e38eec7167dfc4',
  'Mson',
  41.37280423695585,
  2.128722454223953,
  'C. Bacardí, 31 (C. Sugranyes), 08028 Barcelona Cataluña, España',
  251,
  False,
  427138.2938704959,
  4580509.391376183),
 '59419af506fb6007376c90ec': ('59419af506fb6007376c90ec',
  'Amassame',
  41.375023,
  2.1327457,
  'Carrer de Santa Medir 8, 08028 Barcelona Cataluña, España',
  254,
  True,
  427477.2108730002,
  4580752.340675035),
 '4e75111dae60c32850f7bfc0': ('4e75111dae60c32850f7bfc0',
  'El Candil',
  41.37

In [47]:
map_barcelona = folium.Map(location=barcelona_center, zoom_start=13)
folium.Marker(barcelona_center, popup='Plaza Catalunya').add_to(map_barcelona)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_barcelona)

map_barcelona

Looking good. So now we have all the restaurants in area within few kilometers from Barcelona centre, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology1"></a>

In this project we will direct our efforts on detecting areas of Barcelona that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area approximately 6km around the city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Barcelona center** (Plaza Catalunya). We have also **identified Italian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Barcelona - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Italian restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis1"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. 
First let's count the **number of restaurants in every area candidate**:

In [48]:
#location_restaurants
#df_locations.append['Restaurants in area']
df_locations.head()

Address   Latitude  Longitude              X  \
0          Dàrsena Sud, 08040 Barcelona  41.334521   2.148919  428785.515902   
1    Ml Inflamables, 4, 08040 Barcelona  41.334574   2.156088  429385.515902   
2  Carrer del Port de Ningbó, Barcelona  41.334626   2.163258  429985.515902   
3                                 Spain  41.334678   2.170428  430585.515902   
4                                 Spain  41.334730   2.177598  431185.515902   

              Y  Distance from center  
0  4.576243e+06           5992.495307  
1  4.576243e+06           5840.376700  
2  4.576243e+06           5747.173218  
3  4.576243e+06           5715.767665  
4  4.576243e+06           5747.173218

In [50]:
location_restaurants_count = [len(res) for res in location_restaurants]

#df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 13.847222222222221


Address   Latitude  Longitude  \
0                 Dàrsena Sud, 08040 Barcelona  41.334521   2.148919   
1           Ml Inflamables, 4, 08040 Barcelona  41.334574   2.156088   
2         Carrer del Port de Ningbó, Barcelona  41.334626   2.163258   
3                                        Spain  41.334678   2.170428   
4                                        Spain  41.334730   2.177598   
5                                        Spain  41.334781   2.184768   
6                                        Spain  41.334831   2.191938   
7                Unnamed Road, 08040 Barcelona  41.339121   2.138102   
8  Via Circulació del Nord, 8, 08040 Barcelona  41.339175   2.145272   
9           Ml Inflamables, 1, 08040 Barcelona  41.339228   2.152443   

               X             Y  Distance from center  
0  428785.515902  4.576243e+06           5992.495307  
1  429385.515902  4.576243e+06           5840.376700  
2  429985.515902  4.576243e+06           5747.173218  
3  430585.515902  4.576243e+06           5715.767665  
4  431185.515902  4.576243e+06           5747.173218  
5  431785.515902  4.576243e+06           5840.376700  
6  432385.515902  4.576243e+06           5992.495307  
7  427885.515902  4.576762e+06           5855.766389  
8  428485.515902  4.576762e+06           5604.462508  
9  429085.515902  4.576762e+06           5408.326913

OK, now let's calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [51]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [52]:
df_locations.head(10)

Address   Latitude  Longitude  \
0                 Dàrsena Sud, 08040 Barcelona  41.334521   2.148919   
1           Ml Inflamables, 4, 08040 Barcelona  41.334574   2.156088   
2         Carrer del Port de Ningbó, Barcelona  41.334626   2.163258   
3                                        Spain  41.334678   2.170428   
4                                        Spain  41.334730   2.177598   
5                                        Spain  41.334781   2.184768   
6                                        Spain  41.334831   2.191938   
7                Unnamed Road, 08040 Barcelona  41.339121   2.138102   
8  Via Circulació del Nord, 8, 08040 Barcelona  41.339175   2.145272   
9           Ml Inflamables, 1, 08040 Barcelona  41.339228   2.152443   

               X             Y  Distance from center  \
0  428785.515902  4.576243e+06           5992.495307   
1  429385.515902  4.576243e+06           5840.376700   
2  429985.515902  4.576243e+06           5747.173218   
3  430585.515902  4.576243e+06           5715.767665   
4  431185.515902  4.576243e+06           5747.173218   
5  431785.515902  4.576243e+06           5840.376700   
6  432385.515902  4.576243e+06           5992.495307   
7  427885.515902  4.576762e+06           5855.766389   
8  428485.515902  4.576762e+06           5604.462508   
9  429085.515902  4.576762e+06           5408.326913   

   Distance to Italian restaurant  
0                     4231.131955  
1                     4191.232105  
2                     4236.788348  
3                     4365.125937  
4                     4544.690153  
5                     4510.751850  
6                     4556.265566  
7                     3843.491570  
8                     3775.565700  
9                     3682.233738

In [53]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 1465.343661241832


OK, so **on average Italian restaurant can be found within ~1,500m** from every area center candidate. That's not fairly close, so we need to filter our areas further!

In [54]:
# barna_boroughs = bcncity_data
bcncity_data.head()


Borough                           Neighborhood      Latitude    Longitude
0   BARRI                               el Raval  4.581121e+06  430624.9313
1   BARRI                         el Barri Gòtic  4.581289e+06  431291.4440
2   BARRI                         la Barceloneta  4.581448e+06  432355.6530
3   BARRI  Sant Pere, Santa Caterina i la Ribera  4.581984e+06  431707.9381
4   BARRI                          el Fort Pienc  4.583261e+06  431580.2748

In [55]:
def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [56]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [57]:
from folium import plugins
from folium.plugins import HeatMap

map_barcelona = folium.Map(location=barcelona_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_barcelona) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_barcelona)
folium.Marker(barcelona_center).add_to(map_barcelona)
folium.Circle(barcelona_center, radius=1000, fill=False, color='white').add_to(map_barcelona)
folium.Circle(barcelona_center, radius=2000, fill=False, color='white').add_to(map_barcelona)
folium.Circle(barcelona_center, radius=3000, fill=False, color='white').add_to(map_barcelona)
#folium.GeoJson(bcncity_data, style_function=boroughs_style, name='geojson').add_to(map_barcelona)

# add markers to map
for lat, lng, name, category in zip(bcncity_data['Latitude'], bcncity_data['Longitude'], bcncity_data['Neighborhood'], bcncity_data['Borough']):
    label = '{}, {}'.format(name, category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='white',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_barcelona) 


map_barcelona

Looks like a few pockets of low restaurant density closest to city center can be found **north-east and south-west from Plaza Catalunya**. 

Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

In [58]:
map_barcelona = folium.Map(location=barcelona_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_barcelona) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_barcelona)
folium.Marker(barcelona_center).add_to(map_barcelona)
folium.Circle(barcelona_center, radius=1000, fill=False, color='white').add_to(map_barcelona)
folium.Circle(barcelona_center, radius=2000, fill=False, color='white').add_to(map_barcelona)
folium.Circle(barcelona_center, radius=3000, fill=False, color='white').add_to(map_barcelona)
#folium.GeoJson(bcncity_data, style_function=boroughs_style, name='geojson').add_to(map_barcelona)
   
map_barcelona

This map is not so 'hot' (Italian restaurants represent a subset of ~13.5% of all restaurants in Barcelona) but it also indicates higher density of existing Italian restaurants directly north-west from Plaza Catalunya, with closest pockets of **low Italian restaurant density positioned north-east and south-west from city center**.

Based on this we will now focus our analysis on areas *north-east and south-west from the city center* - we will move the center of our area of interest and reduce it's size to have a radius of **3km**. This places our location candidates mostly in boroughs **Hostafrancs and Poblenou** which we will check whether they have popular places where locals and tourist come by often.

### Hostafrancs and Poblenou

Analysis of popular travel guides and web sites often mention Kreuzberg and Friedrichshain as beautifull, interesting, rich with culture, 'hip' and 'cool' Berlin neighborhoods popular with tourists and loved by Berliners.

*"Hostafrancs is a neighbourhood in the Sants-Montjuïc district of Barcelona, Catalonia, Spain. 
Originally the land of the neighbourhood belonged to the former municipality of Santa Maria de Sants, the current district. In 1839 the Provincial Council was to disassociate the sector was the Pont d'en Rabassa Cross to cover for him in Barcelona."(Wikipedia)

*"The neighbourhood's proximity to the centre of Barcelona, together with its retail offering, make it one of Barcelona's most visited and popular districts. And tucked away behind its shopping streets is a maze of narrow streets with a true village feel, which you are bound to be surprised by. The Parc de l'Espanya Industrial, located on the site of a textile mill, and the local markets of Sants and Hostafrancs, are other essential places to visit in the neighbourhood." (Visit Barcelona website).

*"El Poblenou (Catalan pronunciation: [əl ˌpɔbːləˈnɔw]; Catalan for '"new village"') is an extensive neighborhood of Barcelona (Sant Martí district) that borders the Mediterranean Sea to the south, Sant Adrià del Besòs to the east, Parc de la Ciutadella in Ciutat Vella to the west, and Horta-Guinardó and Sant Andreu to the north. It is technically part of the Eixample, its layout having been drafted by Ildefons Cerdà, although the historic center of the neighborhood (which was once a town entirely separated from Barcelona) predates the grid."(Wikipedia)

*"Poblenou, in the Sant Martí district, is a box of surprises. A stroll through its streets reveals striking examples of interesting industrial architecture, such as Can Felipa. In the old part of the district, the Rambla, which can stand comparison with the best of Barcelona's boulevards, is lined with elegant buildings and pavement cafés where you can sit and enjoy this part of the city." (Visit Barcelona website).


Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Hostafrancs and Poblenou closest to Plaza Catalunya.

## Explore the locations in terms of popular places on Foursquare

In [59]:
import requests
radius = 3000

In [60]:
bcncity_data.head()


Borough                           Neighborhood      Latitude    Longitude
0   BARRI                               el Raval  4.581121e+06  430624.9313
1   BARRI                         el Barri Gòtic  4.581289e+06  431291.4440
2   BARRI                         la Barceloneta  4.581448e+06  432355.6530
3   BARRI  Sant Pere, Santa Caterina i la Ribera  4.581984e+06  431707.9381
4   BARRI                          el Fort Pienc  4.583261e+06  431580.2748

In [61]:
address = 'Hostafrancs, Barcelona, Spain'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
newlat = location.latitude
newlong = location.longitude
print(newlat, newlong)

41.3750877 2.1429334


In [62]:
# @hidden cell
urlHost = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(client_id, client_secret, newlat, newlong, version, radius, limit)
urlHost

'https://api.foursquare.com/v2/venues/explore?client_id=0SNKFIVOMYF1JOTTLWIRLO55QF11PAMDVGXXQ3OGZFMBYE53&client_secret=3TJE0KSUGPF0ZXYZQUS4HRRLMFSUQ403Q4WMSPZD2SDEOG4F&ll=41.3750877,2.1429334&v=20190604&radius=3000&limit=2000'

In [66]:
resultsHost = requests.get(urlHost).json()
#resultsHost

In [67]:
address = 'Poblenou, Barcelona, Spain'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
newlat2 = location.latitude
newlong2 = location.longitude
print(newlat2, newlong2)

41.400527 2.2017292


In [68]:
# @hidden cell
urlHost2 = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(client_id, client_secret, newlat2, newlong2, version, radius, limit)
urlHost2

'https://api.foursquare.com/v2/venues/explore?client_id=0SNKFIVOMYF1JOTTLWIRLO55QF11PAMDVGXXQ3OGZFMBYE53&client_secret=3TJE0KSUGPF0ZXYZQUS4HRRLMFSUQ403Q4WMSPZD2SDEOG4F&ll=41.400527,2.2017292&v=20190604&radius=3000&limit=2000'

In [69]:
resultsHost2 = requests.get(urlHost).json()
#resultsHost2

#### Examine results

In [70]:
resultsHost = requests.get(urlHost).json()
'There are {} around Hostafrancs.'.format(len(resultsHost['response']['groups'][0]['items']))

'There are 100 around Hostafrancs.'

In [72]:
items1 = resultsHost['response']['groups'][0]['items']
items1[0]

{'reasons': {'count': 0,
  'items': [{'summary': 'This spot is popular',
    'type': 'general',
    'reasonName': 'globalInteractionReason'}]},
 'venue': {'id': '5831a67ccc05d15be8a8136f',
  'name': 'La Vicoca',
  'location': {'address': 'Hostafrancs de Sió, 18',
   'crossStreet': 'Entre Vilardell y Leiva',
   'lat': 41.374161,
   'lng': 2.144223,
   'labeledLatLngs': [{'label': 'display', 'lat': 41.374161, 'lng': 2.144223}],
   'distance': 149,
   'postalCode': '08014',
   'cc': 'ES',
   'city': 'Barcelona',
   'state': 'Cataluña',
   'country': 'España',
   'formattedAddress': ['Hostafrancs de Sió, 18 (Entre Vilardell y Leiva)',
    '08014 Barcelona Cataluña',
    'España']},
  'categories': [{'id': '4bf58dd8d48988d123941735',
    'name': 'Wine Bar',
    'pluralName': 'Wine Bars',
    'shortName': 'Wine Bar',
    'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/winery_',
     'suffix': '.png'},
    'primary': True}],
  'photos': {'count': 0, 'groups': []},
  'venuePage

In [73]:
resultsHost2 = requests.get(urlHost2).json()
'There are {} around Poblenou.'.format(len(resultsHost2['response']['groups'][0]['items']))

'There are 100 around Poblenou.'

In [74]:
items2 = resultsHost2['response']['groups'][0]['items']
items2[0]

{'reasons': {'count': 0,
  'items': [{'summary': 'This spot is popular',
    'type': 'general',
    'reasonName': 'globalInteractionReason'}]},
 'venue': {'id': '5034b740e4b0ab0c7394518a',
  'name': 'Cruixent BCN',
  'location': {'address': 'Pujades, 173',
   'crossStreet': 'Rbla. Poblenou',
   'lat': 41.40188991912975,
   'lng': 2.20072980500845,
   'labeledLatLngs': [{'label': 'display',
     'lat': 41.40188991912975,
     'lng': 2.20072980500845}],
   'distance': 173,
   'postalCode': '08005',
   'cc': 'ES',
   'city': 'Barcelona',
   'state': 'Cataluña',
   'country': 'España',
   'formattedAddress': ['Pujades, 173 (Rbla. Poblenou)',
    '08005 Barcelona Cataluña',
    'España']},
  'categories': [{'id': '4bf58dd8d48988d16a941735',
    'name': 'Bakery',
    'pluralName': 'Bakeries',
    'shortName': 'Bakery',
    'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/bakery_',
     'suffix': '.png'},
    'primary': True}],
  'photos': {'count': 0, 'groups': []}},
 'referra

In [76]:
dataframe1 = json_normalize(items1) # flatten JSON

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter columns
filtered_columns1 = ['venue.name', 'venue.categories'] + [col for col in dataframe1.columns if col.startswith('venue.location.')] + ['venue.id']
dataframe_filtered1 = dataframe1.loc[:, filtered_columns1]

# filter the category for each row
dataframe_filtered1['venue.categories'] = dataframe_filtered1.apply(get_category_type, axis=1)

# clean columns
dataframe_filtered1.columns = [col.split('.')[-1] for col in dataframe_filtered1.columns]

dataframe_filtered1.head(10)

name                categories  \
0                          La Vicoca                  Wine Bar   
1                 La Caleta de Sants                Restaurant   
2                     Zumzeig Cinema       Indie Movie Theater   
3                          Petit Pau  Mediterranean Restaurant   
4  Plaça d'Espanya (Plaza de España)                     Plaza   
5                         Casa Vives              Dessert Shop   
6                       La Mestressa          Tapas Restaurant   
7                   La terrassa Miró                       Bar   
8                            Tartela                      Café   
9                      Morrow Coffee               Coffee Shop   

                                    address              crossStreet  \
0                    Hostafrancs de Sió, 18  Entre Vilardell y Leiva   
1                   Ctra. de la Bordeta, 54                      NaN   
2                              C. Béjar, 53                      NaN   
3                 C. Espanya Industrial, 22                      NaN   
4                             Pl. d'Espanya                      NaN   
5                              C. Sants, 74                      NaN   
6                           Plaça d'Osca, 7                      NaN   
7                             Tarragona 129                      NaN   
8                             C. Llançà, 32                Diputació   
9  Av. Gran Via de les Corts Catalanes, 403                 Vilamarí   

         lat       lng                                     labeledLatLngs  \
0  41.374161  2.144223  [{'label': 'display', 'lat': 41.374161, 'lng':...   
1  41.373525  2.145157  [{'label': 'display', 'lat': 41.37352504116426...   
2  41.377350  2.145076  [{'label': 'display', 'lat': 41.37734966171251...   
3  41.376266  2.140496  [{'label': 'display', 'lat': 41.37626588093834...   
4  41.375021  2.149115  [{'label': 'display', 'lat': 41.37502128798987...   
5  41.375408  2.137171  [{'label': 'display', 'lat': 41.37540756780608...   
6  41.376050  2.138702  [{'label': 'display', 'lat': 41.37604998013339...   
7  41.377356  2.146089  [{'label': 'display', 'lat': 41.37735601031151...   
8  41.377159  2.149722  [{'label': 'display', 'lat': 41.377159, 'lng':...   
9  41.377105  2.151378  [{'label': 'display', 'lat': 41.37710480525754...   

   distance postalCode  cc       city     state country  \
0       149      08014  ES  Barcelona  Cataluña  España   
1       254      08014  ES  Barcelona  Cataluña  España   
2       308      08014  ES  Barcelona  Cataluña  España   
3       242      08014  ES  Barcelona  Cataluña  España   
4       516      08015  ES  Barcelona  Cataluña  España   
5       482      08014  ES  Barcelona  Cataluña  España   
6       369      08014  ES  Barcelona  Cataluña  España   
7       365      08014  ES  Barcelona  Cataluña  España   
8       612      08015  ES  Barcelona  Cataluña  España   
9       740      08015  ES  Barcelona  Cataluña  España   

                                    formattedAddress  \
0  [Hostafrancs de Sió, 18 (Entre Vilardell y Lei...   
1  [Ctra. de la Bordeta, 54, 08014 Barcelona Cata...   
2   [C. Béjar, 53, 08014 Barcelona Cataluña, España]   
3  [C. Espanya Industrial, 22, 08014 Barcelona Ca...   
4  [Pl. d'Espanya, 08015 Barcelona Cataluña, España]   
5   [C. Sants, 74, 08014 Barcelona Cataluña, España]   
6  [Plaça d'Osca, 7, 08014 Barcelona Cataluña, Es...   
7  [Tarragona 129, 08014 Barcelona Cataluña, España]   
8  [C. Llançà, 32 (Diputació), 08015 Barcelona Ca...   
9  [Av. Gran Via de les Corts Catalanes, 403 (Vil...   

                     neighborhood                        id  
0                             NaN  5831a67ccc05d15be8a8136f  
1                             NaN  4d836b6250913704771f685b  
2                             NaN  524bf13911d2f5fbb7a4ec4e  
3                             NaN  5297a76b11d2ab52764de108  
4                             NaN  4b7c12aff964a520517b2fe3  
5                        

In [77]:
dataframe1.shape

(100, 24)

In [78]:
dataframe2 = json_normalize(items2) # flatten JSON

# filter columns
filtered_columns2 = ['venue.name', 'venue.categories'] + [col for col in dataframe2.columns if col.startswith('venue.location.')] + ['venue.id']
dataframe_filtered2 = dataframe2.loc[:, filtered_columns2]

# filter the category for each row
dataframe_filtered2['venue.categories'] = dataframe_filtered2.apply(get_category_type, axis=1)

# clean columns
dataframe_filtered2.columns = [col.split('.')[-1] for col in dataframe_filtered2.columns]

dataframe_filtered2.head(10)

name              categories  \
0                      Cruixent BCN                  Bakery   
1  La Cervecita Nuestra de Cada Día              Beer Store   
2                          Melocomo      Italian Restaurant   
3                    La Tavernícola  Argentinian Restaurant   
4                  Dino's Ice Cream          Ice Cream Shop   
5               Rambla del Poblenou                    Road   
6                 Le Cinquante Huit               Gastropub   
7                         Can Dendê          Breakfast Spot   
8                       Little Fern          Breakfast Spot   
9                        El Tío Che          Ice Cream Shop   

                        address          crossStreet        lat       lng  \
0                  Pujades, 173       Rbla. Poblenou  41.401890  2.200730   
1                 C. Llull, 184  Rambla del Poblenou  41.400454  2.201477   
2        Carrer de Pujades, 188                  NaN  41.401788  2.200996   
3               Roc Boronat, 70     Calle De Pujades  41.400349  2.197909   
4           Rambla Poble Nou 59                 Llul  41.400910  2.201478   
5           Rambla del Poblenou                  NaN  41.401471  2.200484   
6       Rambla del Poblenou, 58                  NaN  41.400653  2.202557   
7      C. Ciutat de Granada, 44          C. de Llull  41.398296  2.198360   
8               C. Pere IV, 168           C. Llacuna  41.402232  2.197312   
9  Rambla del Poblenou, 44, TDA                  NaN  41.400106  2.202770   

                                      labeledLatLngs  distance postalCode  cc  \
0  [{'label': 'display', 'lat': 41.40188991912975...       173      08005  ES   
1  [{'label': 'display', 'lat': 41.40045398203872...        22      08005  ES   
2  [{'label': 'display', 'lat': 41.401788, 'lng':...       153      08005  ES   
3  [{'label': 'display', 'lat': 41.40034854684869...       319      08005  ES   
4  [{'label': 'display', 'lat': 41.40091005092279...        47      08005  ES   
5  [{'label': 'display', 'lat': 41.40147120183829...       147      08005  ES   
6  [{'label': 'display', 'lat': 41.40065308537522...        70      08005  ES   
7  [{'label': 'display', 'lat': 41.39829633168689...       375      08005  ES   
8  [{'label': 'display', 'lat': 41.40223206041831...       414      08005  ES   
9  [{'label': 'display', 'lat': 41.400105667, 'ln...        98      08005  ES   

        city     state country  \
0  Barcelona  Cataluña  España   
1  Barcelona  Cataluña  España   
2  Barcelona  Cataluña  España   
3  Barcelona  Cataluña  España   
4  Barcelona  Cataluña  España   
5  Barcelona  Cataluña  España   
6  Barcelona  Cataluña  España   
7  Barcelona  Cataluña  España   
8  Barcelona  Cataluña  España   
9  Barcelona  Cataluña  España   

                                    formattedAddress neighborhood  \
0  [Pujades, 173 (Rbla. Poblenou), 08005 Barcelon...          NaN   
1  [C. Llull, 184 (Rambla del Poblenou), 08005 Ba...          NaN   
2  [Carrer de Pujades, 188, 08005 Barcelona Catal...          NaN   
3  [Roc Boronat, 70 (Calle De Pujades), 08005 Bar...          NaN   
4  [Rambla Poble Nou 59 (Llul), 08005 Barcelona C...          NaN   
5  [Rambla del Poblenou, 08005 Barcelona Cataluña...          NaN   
6  [Rambla del Poblenou, 58, 08005 Barcelona Cata...          NaN   
7  [C. Ciutat de Granada, 44 (C. de Llull), 08005...          NaN   
8  [C. Pere IV, 168 (C. Llacuna), 08005 Barcelona...          NaN   
9  [Rambla del Poblenou, 44, TDA, 08005 Barcelona...          NaN   

                         id  
0  5034b740e4b0ab0c7394518a  
1  4b842526f964a520a32331e3  
2  4bb37c412397b713cc2938b3  
3  56b519c4498e81e730fba505  
4  53ebc250498e1a57e50f2f74  
5  4c3f01961ef0d13a4f069380  
6  51c75da9498ee2e84dede473  
7  5469e572498edc6b88d8c1fd  
8  5af2b83ee7a237002c007e3c  
9  4bba21a7935e95213bc62790

In [79]:
dataframe2.shape

(100, 22)

# clean columns
dataframe_filtered.columns = [col.split('.')[-1] for col in dataframe_filtered.columns]

dataframe_filtered.head(10)

In [80]:
# clean column names by keeping only last term
dataframe_filtered1.columns = [column.split('.')[-1] for column in dataframe_filtered1.columns]

dataframe_filtered1.head()




name                categories  \
0                          La Vicoca                  Wine Bar   
1                 La Caleta de Sants                Restaurant   
2                     Zumzeig Cinema       Indie Movie Theater   
3                          Petit Pau  Mediterranean Restaurant   
4  Plaça d'Espanya (Plaza de España)                     Plaza   

                     address              crossStreet        lat       lng  \
0     Hostafrancs de Sió, 18  Entre Vilardell y Leiva  41.374161  2.144223   
1    Ctra. de la Bordeta, 54                      NaN  41.373525  2.145157   
2               C. Béjar, 53                      NaN  41.377350  2.145076   
3  C. Espanya Industrial, 22                      NaN  41.376266  2.140496   
4              Pl. d'Espanya                      NaN  41.375021  2.149115   

                                      labeledLatLngs  distance postalCode  cc  \
0  [{'label': 'display', 'lat': 41.374161, 'lng':...       149      08014  ES   
1  [{'label': 'display', 'lat': 41.37352504116426...       254      08014  ES   
2  [{'label': 'display', 'lat': 41.37734966171251...       308      08014  ES   
3  [{'label': 'display', 'lat': 41.37626588093834...       242      08014  ES   
4  [{'label': 'display', 'lat': 41.37502128798987...       516      08015  ES   

        city     state country  \
0  Barcelona  Cataluña  España   
1  Barcelona  Cataluña  España   
2  Barcelona  Cataluña  España   
3  Barcelona  Cataluña  España   
4  Barcelona  Cataluña  España   

                                    formattedAddress neighborhood  \
0  [Hostafrancs de Sió, 18 (Entre Vilardell y Lei...          NaN   
1  [Ctra. de la Bordeta, 54, 08014 Barcelona Cata...          NaN   
2   [C. Béjar, 53, 08014 Barcelona Cataluña, España]          NaN   
3  [C. Espanya Industrial, 22, 08014 Barcelona Ca...          NaN   
4  [Pl. d'Espanya, 08015 Barcelona Cataluña, España]          NaN   

                         id  
0  5831a67ccc05d15be8a8136f  
1  4d836b6250913704771f685b  
2  524bf13911d2f5fbb7a4ec4e  
3  5297a76b11d2ab52764de108  
4  4b7c12aff964a520517b2fe3

In [81]:
# clean column names by keeping only last term
dataframe_filtered2.columns = [column.split('.')[-1] for column in dataframe_filtered2.columns]

dataframe_filtered2.head()


name              categories  \
0                      Cruixent BCN                  Bakery   
1  La Cervecita Nuestra de Cada Día              Beer Store   
2                          Melocomo      Italian Restaurant   
3                    La Tavernícola  Argentinian Restaurant   
4                  Dino's Ice Cream          Ice Cream Shop   

                  address          crossStreet        lat       lng  \
0            Pujades, 173       Rbla. Poblenou  41.401890  2.200730   
1           C. Llull, 184  Rambla del Poblenou  41.400454  2.201477   
2  Carrer de Pujades, 188                  NaN  41.401788  2.200996   
3         Roc Boronat, 70     Calle De Pujades  41.400349  2.197909   
4     Rambla Poble Nou 59                 Llul  41.400910  2.201478   

                                      labeledLatLngs  distance postalCode  cc  \
0  [{'label': 'display', 'lat': 41.40188991912975...       173      08005  ES   
1  [{'label': 'display', 'lat': 41.40045398203872...        22      08005  ES   
2  [{'label': 'display', 'lat': 41.401788, 'lng':...       153      08005  ES   
3  [{'label': 'display', 'lat': 41.40034854684869...       319      08005  ES   
4  [{'label': 'display', 'lat': 41.40091005092279...        47      08005  ES   

        city     state country  \
0  Barcelona  Cataluña  España   
1  Barcelona  Cataluña  España   
2  Barcelona  Cataluña  España   
3  Barcelona  Cataluña  España   
4  Barcelona  Cataluña  España   

                                    formattedAddress neighborhood  \
0  [Pujades, 173 (Rbla. Poblenou), 08005 Barcelon...          NaN   
1  [C. Llull, 184 (Rambla del Poblenou), 08005 Ba...          NaN   
2  [Carrer de Pujades, 188, 08005 Barcelona Catal...          NaN   
3  [Roc Boronat, 70 (Calle De Pujades), 08005 Bar...          NaN   
4  [Rambla Poble Nou 59 (Llul), 08005 Barcelona C...          NaN   

                         id  
0  5034b740e4b0ab0c7394518a  
1  4b842526f964a520a32331e3  
2  4bb37c412397b713cc2938b3  
3  56b519c4498e81e730fba505  
4  53ebc250498e1a57e50f2f74

#### Let's visualize these items on the map around our location

In [93]:
print(latitude, longitude)
map_barcelona = folium.Map(location=[latitude, longitude], zoom_start=13) # generate map centred Bcn Center

folium.Marker(barcelona_center, popup='Plaza Catalunya').add_to(map_barcelona)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_barcelona)
map_barcelona

# add Center as a red circle mark
folium.features.CircleMarker(
    [latitude, longitude],
    radius=6,
    popup='Center',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
    ).add_to(map_barcelona)

# add Hostafrancs markers to map
for lat, lng, name, category in zip(dataframe_filtered1['lat'], dataframe_filtered1['lng'], dataframe_filtered1['name'], dataframe_filtered1['categories']):
    label = '{}, {}'.format(name, category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='orange',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_barcelona) 

# add Poblenou markers to map
for lat, lng, name, category in zip(dataframe_filtered2['lat'], dataframe_filtered2['lng'], dataframe_filtered2['name'], dataframe_filtered2['categories']):
    label = '{}, {}'.format(name, category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='yellow',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_barcelona) 

# display map
map_barcelona

41.3861586 2.169774


Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Hostafrancs and Poblenou closest to Plaza Catalunya.

Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant** to Hostafrancs and Poblenou.


We might just want to explore only **Hostafrancs** given the higher number of popular places in the area also considering the amount of **Italian restaurants** nearby.


In [98]:
address = 'Hostafrancs, Barcelona, Spain'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
newlat = location.latitude
newlong = location.longitude
print(newlat, newlong)

41.3750877 2.1429334


In [101]:
import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Hostafrancs longitude={}, latitude={}'.format(newlong, newlat))
x, y = lonlat_to_xy(newlong, newlat)
print('Hostafrancs UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Hostafrancs longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Hostafrancs longitude=2.1429334, latitude=41.3750877
Hostafrancs UTM X=428329.2206318337, Y=4580751.049369247
Hostafrancs longitude=2.1429334000000004, latitude=41.375087699999995


/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:6: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  if sys.path[0] == '':


In [99]:
address = 'Poblenou, Barcelona, Spain'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
newlat2 = location.latitude
newlong2 = location.longitude
print(newlat2, newlong2)

41.400527 2.2017292


In [102]:
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Poblenou longitude={}, latitude={}'.format(newlong2, newlat2))
x, y = lonlat_to_xy(newlong2, newlat2)
print('Poblenou UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Poblenou longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Poblenou longitude=2.2017292, latitude=41.400527
Poblenou UTM X=433271.9816509482, Y=4583528.3290184485
Poblenou longitude=2.2017292000000004, latitude=41.400527000000004


/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  after removing the cwd from sys.path.
/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:10: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # Remove the CWD from sys.path while we load stuff.


In [111]:
roi_xs = [428329.2206318337,433271.9816509482]
roi_ys = [4580751.049369247,4583528.3290184485]
roi_latitudes = [41.3750877,41.400527]
roi_longitudes = [2.1429334,2.2017292]

In [112]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [113]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)

Latitude  Longitude              X             Y  Restaurants nearby  \
0  41.375088   2.142933  428329.220632  4.580751e+06                  12   
1  41.400527   2.201729  433271.981651  4.583528e+06                   4   

   Distance to Italian restaurant  
0                      357.265635  
1                      527.250781

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 250 meters**.

In [115]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=250)
print('Locations with no Italian restaurants within 250m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 0
Locations with no Italian restaurants within 250m: 2
Locations with both conditions met: 0


In [135]:
df_good_locations2 = df_roi_locations[good_ita_distance]
df_good_locations2 

Latitude  Longitude              X             Y  Restaurants nearby  \
0  41.375088   2.142933  428329.220632  4.580751e+06                  12   
1  41.400527   2.201729  433271.981651  4.583528e+06                   4   

   Distance to Italian restaurant  
0                      357.265635  
1                      527.250781

In [136]:
good_latitudes = df_good_locations2['Latitude'].values
good_longitudes = df_good_locations2['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [137]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lat, lon in good_locations:
    addr = get_address(api_key, lat, lon).replace(', Spain', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, barcelona_center_x, barcelona_center_y)
    print('{}{} => {:.1f}km from Plaza Catalunya'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis



/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  after removing the cwd from sys.path.


Carrer de la Creu Coberta, 99, 08014 Barcelona     => 2.6km from Plaza Catalunya
Carrer de Llull, 186, 08005 Barcelona              => 3.1km from Plaza Catalunya


/Users/rafadiazrios/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  after removing the cwd from sys.path.


This concludes our analysis. We have created 12 addresses representing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (both around 3km from Plaza Catalunya). 
These locations should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. The zones located in Hostafrancs and Poblenou boroughs, which we have identified as interesting due to being popular with tourists, are fairly close to city center and well connected by public transport.

In [138]:
map_barcelona2 = folium.Map(barcelona_center, zoom_start=14)
folium.Marker(barcelona_center).add_to(map_barcelona2)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=6, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_barcelona2)
map_barcelona2

## Results and Discussion <a name="results1"></a>

Our analysis shows that although there is a great number of restaurants in Barcelona (2500+ in our initial area of interest which was 6x6km around Plaza Catalunya), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected north-west and south from Plaza Catalunya, so we focused our attention to areas south-west and north-east, corresponding to boroughs Hostafrancs and Poblenou, which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow areas of interest, we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 250m were removed.

Those location candidates were zones of interest which contain a number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 2 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Barcelona center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion1"></a>

Purpose of this project was to identify Barcelona areas close to center with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Hostafrancs and Poblenou), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.

## The End